In [8]:
from geopy.distance import geodesic
import numpy as np
import requests
headers = {
    'user-agent': 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/114.0.0.0 Safari/537.36',
}


In [9]:
def get_square_array(square_size: int = 300) -> dict:
    south_lat = 41.185
    north_lat = 81.857
    west_lon = 19.641
    east_lon = 190.95
    num_squares_lat = int(geodesic((south_lat, west_lon), (north_lat, west_lon)).km // square_size)
    num_squares_lon = int(geodesic((south_lat, west_lon), (south_lat, east_lon)).km // square_size)
    lats = np.linspace(south_lat, north_lat, num_squares_lat)
    lons = np.linspace(west_lon, east_lon, num_squares_lon)
    squares = []
    for i in range(num_squares_lat-1):
        for j in range(num_squares_lon-1):
            sw = (lats[i], lons[j])
            ne = (lats[i+1], lons[j+1])
            square_str = {
                'ne': f'{ne[0]:.5f},{ne[1]:.5f}',
                'sw': f'{sw[0]:.5f},{sw[1]:.5f}'
            }
            squares.append(square_str)
    return {'square_size': square_size, 'squares': squares}

In [11]:
# режу Россию на квадраты по 300 км
squares_obj = get_square_array(square_size=300)

result_array = []

for index, sqr in enumerate(squares_obj['squares']):
    try:
        # получаю верхний правый и левый нижний углы
        sw = sqr['sw'].split(',')
        ne = sqr['ne'].split(',')
        json_data = {
            'viewPort': {
                'leftLowerCorner': {
                    'lat': sw[0],
                    'lon': sw[1],
                },
                'rightUpperCorner': {
                    'lat': ne[0],
                    'lon': ne[1],
                },
            },
            'isOwn': None,
        }
        response = requests.post('https://opp-api.ozon.ru/pick-point/search', headers=headers, json=json_data)
        points = response.json()['pickPoints']
        if len(points) > 0:
            for p in points:
                result_array.append(p)
        message = f"Квадрат {index + 1} из {len(squares_obj['squares'])}. Точки: {len(points)}."
        print(message.ljust(150), end='\r')
    except Exception as err:
        message = f"Ошибка: {err}."
        print(message.ljust(150), end='\r')

print(f'Собрано {result_array} точки'.ljust(150), end='\r')
# Ошибка: 'pickPoints'. говорит о пустом квадрате

In [13]:
len(result_array)

37430

In [28]:
import json

with open('ozon_points.json', 'w') as f:
    json.dump(result_array, f)